In [1]:
%load_ext autoreload
%autoreload 2
from bokeh.io import push_notebook,show,output_notebook
from bokeh.layouts import row
from bokeh.plotting import figure
from bokeh.models import ColumnDataSource, OpenURL, TapTool, CustomJS,BoxSelectTool,Rect,Ellipse
import numpy as np
from image_vis import *
output_notebook()

Using TensorFlow backend.


Loading BokehJS ...

In [2]:
import matplotlib.image as mpimg
import scipy
file_name='./data_chess/train/chess16.jpg'
#file_name='./data_nuclis/2tg_E103p_223a001/2tg_E103p_223a001.png'
#file_name='./data_nuclis_dev/2tg_E98p_224a001/2tg_E98p_224a001.png'


file_type=1# 1 o 255
img2=open_image(file_name,file_type=1)

x_rand=[]
y_rand=[]
probs=[]
#img2=scipy.misc.imresize(img2,(img2.shape[0]/4,img2.shape[1]/4))
N1,N2=img2.shape[:2]
print img2.shape

(640, 480, 4)


In [4]:
red_points=ImagePoints(img2)
green_points=ImagePoints(img2,'#00FF00','#00FF00')
len(red_points.yg)

0

In [ ]:
red_points.load(file_name)
len(red_points.yg)

In [ ]:
red_points.save(file_name)

In [33]:
t2=visualize_image(img2,[red_points,green_points],'red_points')

In [167]:
red_points.set_data([40,40,440,440],[100,500,100,500])

In [34]:
X=squares_of_board(img2, offset_x=40, offset_y=100, board_size=400)
X.shape

(64, 50, 50, 3)

In [35]:
im_total=image_grid(X, num_rows=8, num_cols=8, w=50, h=50, margin=0)


In [36]:

points=get_image_type_points(im_total,file_name,TYPES)

In [440]:
save_image_type_points(points,file_name)

In [37]:
var='black_kings'
t3=visualize_image(im_total,[points[var]],"points['{0}']".format(var))


In [31]:
dict_indexs=indexs_from_mosaic_points_dict(points,w=50,h=50)

In [41]:
im_total2=image_grid(X[dict_indexs['white_rooks'],:,:,:], num_rows=8, num_cols=8, w=50, h=50, margin=0)
t4=visualize_image(im_total2,[ImagePoints(im_total2)],'none')

In [439]:
Y=np.zeros((X.shape[0],13))
for i,t in enumerate(TYPES):
    Y[dict_indexs[t],i]=1

Y.sum()

64.0

In [22]:
model=build_single_cnn_model(shape=(400,400,3),
                           kernel_size = 10, 
                            pool_size = 2 ,
                            conv_depth_1 = 32 ,
                            conv_depth_2 = 64 ,
                            drop_prob_1 = 0.5 ,
                            hidden_size = 100 ,fully_connected_padding='valid',
                           fully_connected_kernel=(12,12),
                           num_classes=13,out_flat=False)
model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         (None, 400, 400, 3)       0         
_________________________________________________________________
conv2d_13 (Conv2D)           (None, 400, 400, 32)      9632      
_________________________________________________________________
conv2d_14 (Conv2D)           (None, 400, 400, 32)      102432    
_________________________________________________________________
max_pooling2d_5 (MaxPooling2 (None, 200, 200, 32)      0         
_________________________________________________________________
dropout_7 (Dropout)          (None, 200, 200, 32)      0         
_________________________________________________________________
conv2d_15 (Conv2D)           (None, 200, 200, 64)      204864    
_________________________________________________________________
conv2d_16 (Conv2D)           (None, 200, 200, 64)      409664    
__________

In [14]:
file_names=['./data_chess/train/chess{0}.jpg'.format(i) for i in ['7','8','9','10','11','12','13','14','15','16']]
print file_names
X,Y=generate_images_from_chess_files(file_names)
Y.shape

['./data_chess/train/chess7.jpg', './data_chess/train/chess8.jpg', './data_chess/train/chess9.jpg', './data_chess/train/chess10.jpg', './data_chess/train/chess11.jpg', './data_chess/train/chess12.jpg', './data_chess/train/chess13.jpg', './data_chess/train/chess14.jpg', './data_chess/train/chess15.jpg', './data_chess/train/chess16.jpg']


(640, 13)

In [18]:
model.fit(X/255., Y,                # Train the model using the training set...
          batch_size=64, epochs=30,
          verbose=1)

Epoch 1/30
640/640 [==============================] - 0s - loss: 0.0170 - acc: 0.9953     
Epoch 2/30
640/640 [==============================] - 0s - loss: 0.0150 - acc: 0.9938     
Epoch 3/30
640/640 [==============================] - 0s - loss: 0.0203 - acc: 0.9891     
Epoch 4/30
640/640 [==============================] - 0s - loss: 0.0222 - acc: 0.9906     
Epoch 5/30
640/640 [==============================] - 0s - loss: 0.0168 - acc: 0.9922     
Epoch 6/30
640/640 [==============================] - 0s - loss: 0.0223 - acc: 0.9922     
Epoch 7/30
640/640 [==============================] - 0s - loss: 0.0270 - acc: 0.9922     
Epoch 8/30
640/640 [==============================] - 0s - loss: 0.0144 - acc: 0.9953     
Epoch 9/30
640/640 [==============================] - 0s - loss: 0.0139 - acc: 0.9938     
Epoch 10/30
640/640 [==============================] - 0s - loss: 0.0151 - acc: 0.9953     
Epoch 11/30
640/640 [==============================] - 0s - loss: 0.0095 - acc: 0.9953   

In [19]:
model.save_weights('chess_pieces.h5')

In [12]:
model.load_weights('chess_pieces.h5')

In [20]:
im_cut=img2[100:500,40:440]
t=visualize_image(im_cut,[ImagePoints(im_cut)],"hello")
import scipy.misc
scipy.misc.imsave(file_name.replace('.jpg','_cut.jpg'), im_cut)

In [24]:
data=(im_cut[:,:,:3]/255.).reshape(1,400,400,3)
Y=model.predict(data)
#Y.reshape(8,8,13).argmax(axis=2)
Y.shape

(1, 8, 8, 13)

In [164]:
import coremltools
converter=coremltools.converters.keras.convert(model,input_names=['chess_image'],image_input_names=['chess_image'])
converter.save('chess_pieces.mlmodel')

0 : input_16, <keras.engine.topology.InputLayer object at 0x7f80248001d0>
1 : conv2d_91, <keras.layers.convolutional.Conv2D object at 0x7f8024800250>
2 : conv2d_91__activation__, <keras.layers.core.Activation object at 0x7f80245b5f10>
3 : conv2d_92, <keras.layers.convolutional.Conv2D object at 0x7f80248002d0>
4 : conv2d_92__activation__, <keras.layers.core.Activation object at 0x7f80245b5f90>
5 : max_pooling2d_31, <keras.layers.pooling.MaxPooling2D object at 0x7f8024800a90>
6 : conv2d_93, <keras.layers.convolutional.Conv2D object at 0x7f8024829fd0>
7 : conv2d_93__activation__, <keras.layers.core.Activation object at 0x7f802454f050>
8 : conv2d_94, <keras.layers.convolutional.Conv2D object at 0x7f8024829050>
9 : conv2d_94__activation__, <keras.layers.core.Activation object at 0x7f802454f0d0>
10 : max_pooling2d_32, <keras.layers.pooling.MaxPooling2D object at 0x7f80247d1c10>
11 : conv2d_95, <keras.layers.convolutional.Conv2D object at 0x7f80247a40d0>
12 : conv2d_95__activation__, <keras.l

In [ ]:
def dist(x1,x2,y1,y2):
    return ((x1-x2)**2 + (y1-y2)**2)**0.5

def group(values):
    import numpy as np
    values = np.array(values)
    values.sort()
    dif = np.ones(values.shape,values.dtype)
    dif[1:] = np.diff(values)
    idx = np.where(dif>0)
    vals = values[idx]
    count = np.diff(idx)
    return vals

print probs.shape
prob_th=0.5
dist_th=10
clust_th=10
#clust_th=0
x_rand=x_rand[probs>prob_th]
y_rand=y_rand[probs>prob_th]
probs=probs[probs>prob_th]
probs[probs>prob_th].shape,probs.shape
clusters=np.ones((probs.shape[0],))*-1                  
for i in range(probs.shape[0]):
#for i in range(1):
    dists=dist(x_rand,x_rand[i],y_rand,y_rand[i])
    #print "dists",dists
    dist_filter=dists<=dist_th
    #print "dist_filter",np.where(dist_filter)
    without_cluster=np.logical_and(dist_filter,clusters==-1)
    clusters[without_cluster]=i
    different_clusters=group(clusters[dist_filter])
    for c in different_clusters:
        clusters[clusters==c]=i
clust=group(clusters)
x_rand2=[]
y_rand2=[]
for c in clust:
    #print clusters[clusters==c].shape[0]
    if clusters[clusters==c].shape[0]>clust_th:
        x_rand2.append(np.mean(x_rand[clusters==c]))
        y_rand2.append(np.mean(y_rand[clusters==c]))
x_rand=np.array(x_rand2)
y_rand=np.array(y_rand2)

In [ ]:
x_rand.shape

In [ ]:
import numpy as np
np.random.randint(0,2,size=(3,3))

In [ ]:
generate_random_points_with_probs(red_points,green_points,M=10000,percent_negative_filter=5)
#probs

In [ ]:
X,Y=dataset_from_points(green_points)


In [102]:
from keras.datasets import cifar10 # subroutines for fetching the CIFAR-10 dataset
from keras.models import Model # basic class for specifying and training a neural network
from keras.layers import Input, Convolution2D, MaxPooling2D, Dense, Dropout, Flatten
from keras.utils import np_utils # utilities for one-hot encoding of ground truth values
import keras
import numpy as np
inp = Input(shape=(40, 40, 3)) # depth goes last in TensorFlow back-end (first in Theano)
#inp = Input(shape=(612, 816, 3)) # depth goes last in TensorFlow back-end (first in Theano)
#inp = Input(shape=(500, 500, 3)) # depth goes last in TensorFlow back-end (first in Theano)
# Conv [32] -> Conv [32] -> Pool (with dropout on the pooling layer)
conv_1 = Convolution2D(conv_depth_1, (kernel_size, kernel_size), padding='same', activation='relu')(inp)
conv_2 = Convolution2D(conv_depth_1, (kernel_size, kernel_size), padding='same', activation='relu')(conv_1)
pool_1 = MaxPooling2D(pool_size=(pool_size, pool_size))(conv_2)
drop_1 = Dropout(drop_prob_1)(pool_1)
# Conv [64] -> Conv [64] -> Pool (with dropout on the pooling layer)
conv_3 = Convolution2D(conv_depth_2, (kernel_size, kernel_size), padding='same', activation='relu')(drop_1)
conv_4 = Convolution2D(conv_depth_2, (kernel_size, kernel_size), padding='same', activation='relu')(conv_3)
pool_2 = MaxPooling2D(pool_size=(pool_size, pool_size))(conv_4)
drop_2 = Dropout(drop_prob_1)(pool_2)
# Now flatten to 1D, apply FC -> ReLU (with dropout) -> softmax

'''flat = Flatten()(drop_2)
hidden = Dense(hidden_size, activation='relu')(flat)
drop_3 = Dropout(drop_prob_2)(hidden)
out = Dense(2, activation='softmax')(drop_3)'''
#conv_5= Convolution2D(30,(10,10),strides=(1,1),padding='same',activation='relu')(drop_2)
#Per nuclis millor 100
conv_5= Convolution2D(100,(10,10),strides=(1,1),padding='valid',activation='relu')(drop_2)
drop_3= Dropout(drop_prob_1)(conv_5)
conv_6=Convolution2D(2,(1,1),padding='valid',activation='softmax')(drop_3)
out=Flatten()(conv_6)

model = Model(inputs=inp, outputs=out) # To define a model, just specify its input and output layers
adam=keras.optimizers.Adam(lr=0.0001, beta_1=0.9, beta_2=0.999, epsilon=1e-08, decay=0.0)

model.compile(loss='categorical_crossentropy', # using the cross-entropy loss function
              optimizer=adam, # using the Adam optimiser
              metrics=['accuracy']) 
model.summary()
model.layers

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         (None, 40, 40, 3)         0         
_________________________________________________________________
conv2d_1 (Conv2D)            (None, 40, 40, 32)        9632      
_________________________________________________________________
conv2d_2 (Conv2D)            (None, 40, 40, 32)        102432    
_________________________________________________________________
max_pooling2d_1 (MaxPooling2 (None, 20, 20, 32)        0         
_________________________________________________________________
dropout_1 (Dropout)          (None, 20, 20, 32)        0         
_________________________________________________________________
conv2d_3 (Conv2D)            (None, 20, 20, 64)        204864    
_________________________________________________________________
conv2d_4 (Conv2D)            (None, 20, 20, 64)        409664    
__________

In [ ]:
model.fit(X, Y,                # Train the model using the training set...
          batch_size=batch_size, epochs=10,
          verbose=1, validation_split=0.1) 

In [ ]:
model.save_weights('conv_nuclis.h5')

In [ ]:
model.load_weights('conv_chess.h5')

In [ ]:
import coremltools
converter=coremltools.converters.keras.convert(model,input_names=['chess_image'],image_input_names=['chess_image'])
converter.save('chess500x500.mlmodel')

In [ ]:
model.evaluate(X,Y)

In [ ]:
probs=model.predict(X,verbose=1)[:,0]>0.5

In [ ]:
conv_out_y=125
conv_out_x=125
probs=model.predict((img2[:,:,:3]/255.).reshape(1,N1,N2,3)).reshape(conv_out_y,conv_out_x,2)[:,:,0].reshape(-1)>0.95

x_rand=[]
y_rand=[]
for k in range(conv_out_y):
    for u in range(conv_out_x):
        y_rand.append(u*4+4)
        x_rand.append(k*4+4)
x_rand=np.array(x_rand)
y_rand=np.array(y_rand)
'''x_cond=np.logical_and(x_rand>=0,x_rand<=499)
y_cond=np.logical_and(y_rand>=0,y_rand<=499)
cond=np.logical_and(x_cond,y_cond)
probs=probs[cond]
x_rand=x_rand[cond]
y_rand=y_rand[cond]'''


In [ ]:
i=12
im_total=np.zeros((400,400,4))
p4=figure(x_range=(0,400), y_range=(0,400),plot_width=400,plot_height=400)#,tools=[box_select])
for i in range(10):
    for j in range(10):        
        im=(np.concatenate([X[i*10+j],np.ones((40,40,1),dtype=np.float64)],axis=2)*255)
        im_total[i*40:(i+1)*40,j*40:(j+1)*40,:]=im
        
        
print im.shape
p4.image_rgba([im_total.astype(np.uint8)],x=0, y=0, dw=400, dh=400)
for i in range(10):
    for j in range(10): 
        yi=Y[i*10+j,0]
        #print y
        p4.ellipse(x=j*40+20,
            y=i*40+20,
            width=10,
            height=10,
            line_alpha=yi,
            fill_alpha=yi,
            line_color='#00FF00',
            fill_color='#00FF00')
t2=show(p4,notebook_handle=True)
y_rand[0],x_rand[0]


